In [1]:
import numpy as np
import pandas as pd
import os
import time
import librosa
import librosa.display
import IPython
from IPython.display import Audio
from IPython.display import Image
import matplotlib.pyplot as plt

In [2]:
import numpy as np
import pandas as pd
import os
import librosa
import librosa.display
import IPython
from IPython.display import Audio
from IPython.display import Image
import matplotlib.pyplot as plt

EMOTIONS = {1:'neutral', 2:'calm', 3:'happy', 4:'sad', 5:'angry', 6:'fear', 7:'disgust', 0:'surprise'}
DATA_PATH = 'C:/Users/Saransh/Desktop/Research Team/data/RAVDESS/audio_speech_actors_01-24/'
SAMPLE_RATE = 48000

data = pd.DataFrame(columns=['Emotion', 'Emotion intensity', 'Gender','Path'])
for dirname, _, filenames in os.walk(DATA_PATH):
    for filename in filenames:
        file_path = os.path.join('/kaggle/input/',dirname, filename)
        identifiers = filename.split('.')[0].split('-')
        emotion = (int(identifiers[2]))
        if emotion == 8: 
            emotion = 0
        if int(identifiers[3]) == 1:
            emotion_intensity = 'normal' 
        else:
            emotion_intensity = 'strong'
        if int(identifiers[6])%2 == 0:
            gender = 'female'
        else:
            gender = 'male'
        
        data = data.append({"Emotion": emotion,
                            "Emotion intensity": emotion_intensity,
                            "Gender": gender,
                            "Path": file_path
                             },
                             ignore_index = True
                          )

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\3700096665.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append({"Emotion": emotion,
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\3700096665.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append({"Emotion": emotion,
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\3700096665.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append({"Emotion": emotion,
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\3700096665.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append({"Emotion": emotion,
C:\Users\Saransh\AppData

In [3]:
import tensorflow as tf
import time

In [4]:
mel_spectrograms = []
signals = []
for i, file_path in enumerate(data.Path):
    audio, sample_rate = librosa.load(file_path, duration=3, offset=0.5, sr=SAMPLE_RATE)
    signal = np.zeros((int(SAMPLE_RATE*3,)))
    signal[:len(audio)] = audio
    signals.append(signal)
    print("\r Processed {}/{} files".format(i,len(data)),end='')
signals = np.stack(signals,axis=0)

 Processed 1439/1440 files

In [5]:
X = signals
train_ind,test_ind,val_ind = [],[],[]
X_train,X_val,X_test = [],[],[]
Y_train,Y_val,Y_test = [],[],[]
for emotion in range(len(EMOTIONS)):
        emotion_ind = list(data.loc[data.Emotion==emotion,'Emotion'].index)
        emotion_ind = np.random.permutation(emotion_ind)
        m = len(emotion_ind)
        ind_train = emotion_ind[:int(0.8*m)]
        ind_val = emotion_ind[int(0.8*m):int(0.9*m)]
        ind_test = emotion_ind[int(0.9*m):]
        X_train.append(X[ind_train,:])
        Y_train.append(np.array([emotion]*len(ind_train),dtype=np.int32))
        X_val.append(X[ind_val,:])
        Y_val.append(np.array([emotion]*len(ind_val),dtype=np.int32))
        X_test.append(X[ind_test,:])
        Y_test.append(np.array([emotion]*len(ind_test),dtype=np.int32))
        train_ind.append(ind_train)
        test_ind.append(ind_test)
        val_ind.append(ind_val)
X_train = np.concatenate(X_train,0)
X_val = np.concatenate(X_val,0)
X_test = np.concatenate(X_test,0)
Y_train = np.concatenate(Y_train,0)
Y_val = np.concatenate(Y_val,0)
Y_test = np.concatenate(Y_test,0)
train_ind = np.concatenate(train_ind,0)
val_ind = np.concatenate(val_ind,0)
test_ind = np.concatenate(test_ind,0)
print(f'X_train:{X_train.shape}, Y_train:{Y_train.shape}')
print(f'X_val:{X_val.shape}, Y_val:{Y_val.shape}')
print(f'X_test:{X_test.shape}, Y_test:{Y_test.shape}')
# check if all are unique
unique, count = np.unique(np.concatenate([train_ind,test_ind,val_ind],0), return_counts=True)
print("Number of unique indexes is {}, out of {}".format(sum(count==1), X.shape[0]))

del X

X_train:(1147, 144000), Y_train:(1147,)
X_val:(143, 144000), Y_val:(143,)
X_test:(150, 144000), Y_test:(150,)
Number of unique indexes is 1440, out of 1440


In [6]:
def addAWGN(signal, num_bits=16, augmented_num=2, snr_low=15, snr_high=30): 
        signal_len = len(signal)
        # Generate White Gaussian noise
        noise = np.random.normal(size=(augmented_num, signal_len))
        # Normalize signal and noise
        norm_constant = 2.0**(num_bits-1)
        signal_norm = signal / norm_constant
        noise_norm = noise / norm_constant
        # Compute signal and noise power
        s_power = np.sum(signal_norm ** 2) / signal_len
        n_power = np.sum(noise_norm ** 2, axis=1) / signal_len
        # Random SNR: Uniform [15, 30] in dB
        target_snr = np.random.randint(snr_low, snr_high)
        # Compute K (covariance matrix) for each noise 
        K = np.sqrt((s_power / n_power) * 10 ** (- target_snr / 10))
        K = np.ones((signal_len, augmented_num)) * K  
        # Generate noisy signal
        return signal + K.T * noise

In [7]:

aug_signals = []
aug_labels = []
for i in range(X_train.shape[0]):
        signal = X_train[i,:]
        augmented_signals = addAWGN(signal)
        for j in range(augmented_signals.shape[0]):
            aug_labels.append(data.loc[i,"Emotion"])
            aug_signals.append(augmented_signals[j,:])
            data = data.append(data.iloc[i], ignore_index=True)
        print("\r Processed {}/{} files".format(i,X_train.shape[0]),end='')
aug_signals = np.stack(aug_signals,axis=0)
X_train = np.concatenate([X_train,aug_signals],axis=0)
aug_labels = np.stack(aug_labels,axis=0)
Y_train = np.concatenate([Y_train,aug_labels])
print('')
print(f'X_train:{X_train.shape}, Y_train:{Y_train.shape}')


 Processed 8/1147 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 28/1147 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 50/1147 files

...

 Processed 1123/1147 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 1142/1147 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\4050680821.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 1146/1147 files
X_train:(3441, 144000), Y_train:(3441,)


In [8]:
aug_signals = []
aug_labels = []
for i in range(X_train.shape[0]):
        signal = X_train[i,:]
        augmented_signals = addAWGN(signal)
        for j in range(augmented_signals.shape[0]):
            aug_labels.append(data.loc[i,"Emotion"])
            aug_signals.append(augmented_signals[j,:])
            data = data.append(data.iloc[i], ignore_index=True)
        print("\r Processed {}/{} files".format(i,X_train.shape[0]),end='')
aug_signals = np.stack(aug_signals,axis=0)
X_train = np.concatenate([X_train,aug_signals],axis=0)
aug_labels = np.stack(aug_labels,axis=0)
Y_train = np.concatenate([Y_train,aug_labels])
print('')
print(f'X_train:{X_train.shape}, Y_train:{Y_train.shape}')

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 17/3441 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 38/3441 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

...

 Processed 3411/3441 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 3428/3441 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i], ignore_index=True)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\2056559257.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = data.append(data.iloc[i],

 Processed 3440/3441 files
X_train:(10323, 144000), Y_train:(10323,)


In [9]:
def getMELspectrogram(audio, sample_rate):
        mel_spec = librosa.feature.melspectrogram(y=audio,
                                                  sr=sample_rate,
                                                  n_fft=1024,
                                                  win_length = 512,
                                                  window='hamming',
                                                  hop_length = 256,
                                                  n_mels=128,
                                                  fmax=sample_rate/2
                                                 )

        mfcc = librosa.feature.mfcc(y=audio, sr=sample_rate,fmax = sample_rate/2, n_mfcc=10323)
        cqt = librosa.feature.chroma_stft(y = audio, sr= sample_rate,hop_length = 256,n_fft=1024, window='hamming',win_length=512,n_chroma=128)

        mel_spec_db = librosa.power_to_db(mel_spec, ref=np.max)
        cqt_db = librosa.power_to_db(cqt, ref= np.max)
        mfcc_db=librosa.power_to_db(mfcc, ref = np.max )

        
        max_length = max(mel_spec.shape[1], mfcc.shape[1], cqt.shape[1])

        # Resample the shorter features to have the same length as the longest feature
        mel_spec_resampled = librosa.resample(mel_spec, mel_spec.shape[1], max_length)
        mfcc_resampled = librosa.resample(mfcc, mfcc.shape[1], max_length)
        cqt_resampled = librosa.resample(cqt, cqt.shape[1], max_length)
        print(mel_spec_resampled.shape)
        print(cqt_resampled.shape)
        print(mfcc_resampled.shape)

        # Combine resampled features into a single tensor
        features = np.stack([mel_spec_resampled, mfcc_resampled, cqt_resampled], axis=1)  # shape: (batchsize, num_features, time)
        print(features.shape)
        # Reshape tensor to desired shape
        tensor = np.reshape(features, (128, 563, 3))  # shape: (batchsize, 224, 224, 3) 
       
        return tensor

something = getMELspectrogram(signal, SAMPLE_RATE)


C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:23: FutureWarning: Pass orig_sr=563, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mel_spec_resampled = librosa.resample(mel_spec, mel_spec.shape[1], max_length)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:24: FutureWarning: Pass orig_sr=282, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc_resampled = librosa.resample(mfcc, mfcc.shape[1], max_length)


(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)


C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:25: FutureWarning: Pass orig_sr=563, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  cqt_resampled = librosa.resample(cqt, cqt.shape[1], max_length)


In [10]:
something.shape

(128, 563, 3)

In [11]:
import tensorflow as tf

In [12]:
mel_train = []
print("Calculatin mel spectrograms for train set")
for i in range(X_train.shape[0]):
    mel_spectrogram = getMELspectrogram(X_train[i,:], sample_rate=SAMPLE_RATE)
    mel_train.append(mel_spectrogram)
    print("\r Processed {}/{} files".format(i,X_train.shape[0]),end='')
print('')
del X_train

mel_val = []
print("Calculatin mel spectrograms for val set")
for i in range(X_val.shape[0]):
    mel_spectrogram = getMELspectrogram(X_val[i,:], sample_rate=SAMPLE_RATE)
    mel_val.append(mel_spectrogram)
    print("\r Processed {}/{} files".format(i,X_val.shape[0]),end='')
print('')
del X_val

mel_test = []
print("Calculatin mel spectrograms for test set")
for i in range(X_test.shape[0]):
    mel_spectrogram = getMELspectrogram(X_test[i,:], sample_rate=SAMPLE_RATE)
    mel_test.append(mel_spectrogram)
    print("\r Processed {}/{} files".format(i,X_test.shape[0]),end='')
print('')
del X_test

Calculatin mel spectrograms for train set
(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 0/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 1/10323 files

C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:23: FutureWarning: Pass orig_sr=563, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mel_spec_resampled = librosa.resample(mel_spec, mel_spec.shape[1], max_length)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:24: FutureWarning: Pass orig_sr=282, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc_resampled = librosa.resample(mfcc, mfcc.shape[1], max_length)
C:\Users\Saransh\AppData\Local\Temp\ipykernel_6864\359267863.py:25: FutureWarning: Pass orig_sr=563, target_sr=563 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  cqt_resampled = librosa.resample(cqt, cqt.shape[1], max_length)


(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 2/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 3/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 4/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 5/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 6/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 7/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 8/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 9/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 10/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 11/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 12/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 13/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 14/10323 files(128, 563)
(128, 563)
(128, 563)
(128, 3, 563)
 Processed 15/10323 files

In [13]:
import keras
from keras.applications import VGG19

In [14]:
vgg_model = VGG19(weights='imagenet', include_top= False, input_shape=(128,563,3))

In [15]:
for layer in vgg_model.layers:
    layer.trainable = False
# Make sure you have frozen the correct layers
for i, layer in enumerate(vgg_model.layers):
    print(i, layer.name, layer.trainable)

0 input_1 False
1 block1_conv1 False
2 block1_conv2 False
3 block1_pool False
4 block2_conv1 False
5 block2_conv2 False
6 block2_pool False
7 block3_conv1 False
8 block3_conv2 False
9 block3_conv3 False
10 block3_conv4 False
11 block3_pool False
12 block4_conv1 False
13 block4_conv2 False
14 block4_conv3 False
15 block4_conv4 False
16 block4_pool False
17 block5_conv1 False
18 block5_conv2 False
19 block5_conv3 False
20 block5_conv4 False
21 block5_pool False


In [16]:
def splitIntoChunks(mel_spec,win_size,stride):
    t = mel_spec.shape[1]
    num_of_chunks = int(t/stride)
    chunks = []
    for i in range(num_of_chunks):
        chunk = mel_spec[:,i*stride:i*stride+win_size]
        if chunk.shape[1] == win_size:
            chunks.append(chunk)
    return np.stack(chunks,axis=0)

In [17]:
mel_train_chunked = []
for mel_spec in mel_train:
    chunks = splitIntoChunks(mel_spec, win_size=128,stride=64)
    mel_train_chunked.append(chunks)
print("Number of chunks is {}".format(chunks.shape[0]))
# val set
mel_val_chunked = []
for mel_spec in mel_val:
    chunks = splitIntoChunks(mel_spec, win_size=128,stride=64)
    mel_val_chunked.append(chunks)
print("Number of chunks is {}".format(chunks.shape[0]))
# test set
mel_test_chunked = []
for mel_spec in mel_test:
    chunks = splitIntoChunks(mel_spec, win_size=128,stride=64)
    mel_test_chunked.append(chunks)
print("Number of chunks is {}".format(chunks.shape[0]))

Number of chunks is 7
Number of chunks is 7
Number of chunks is 7


In [18]:
def make_train_step(model, loss_fnc, optimizer):
    def train_step(X,Y):
        # set model to train mode
        model.train()
        # forward pass
        output_logits, output_softmax = model(X)
        predictions = torch.argmax(output_softmax,dim=1)
        accuracy = torch.sum(Y==predictions)/float(len(Y))
        # compute loss
        loss = loss_fnc(output_logits, Y)
        # compute gradients
        loss.backward()
        # update parameters and zero gradients
        optimizer.step()
        optimizer.zero_grad()
        return loss.item(), accuracy*100
    return train_step

In [19]:
def make_validate_fnc(model,loss_fnc):
    def validate(X,Y):
        with torch.no_grad():
            model.eval()
            output_logits, output_softmax = model(X)
            predictions = torch.argmax(output_softmax,dim=1)
            accuracy = torch.sum(Y==predictions)/float(len(Y))
            loss = loss_fnc(output_logits,Y)
        return loss.item(), accuracy*100, predictions
    return validate

In [20]:
import tensorflow as tf
import keras 
from keras import Model


x = vgg_model.output
x = tf.keras.layers.Flatten()(x) # Flatten dimensions to for use in FC layers
x = tf.keras.layers.Dense(512, activation='relu')(x)
x = tf.keras.layers.Dropout(0.5)(x) # Dropout layer to reduce overfitting
x = tf.keras.layers.Dense(256, activation='relu')(x)
x = tf.keras.layers.Dense(8, activation='softmax')(x) # Softmax for multiclass
transfer_model = Model(inputs=vgg_model.input, outputs=x)


In [21]:
import numpy as np

X_train = np.stack(mel_train_chunked,axis=0)
X_train = np.expand_dims(X_train,2)
print('Shape of X_train: ',X_train.shape)
X_val = np.stack(mel_val_chunked,axis=0)
X_val = np.expand_dims(X_val,2)
print('Shape of X_val: ',X_val.shape)
X_test = np.stack(mel_test_chunked,axis=0)
X_test = np.expand_dims(X_test,2)
print('Shape of X_test: ',X_test.shape)

Shape of X_train:  (10323, 7, 1, 128, 128, 3)
Shape of X_val:  (143, 7, 1, 128, 128, 3)
Shape of X_test:  (150, 7, 1, 128, 128, 3)


In [22]:
X_train.shape

(10323, 7, 1, 128, 128, 3)

In [24]:
import tensorflow as tf


EPOCHS=100
DATASET_SIZE = X_train.shape[0]
BATCH_SIZE = 128

model = transfer_model()

OPTIMIZER = torch.optim.SGD(model.parameters(),lr=0.01, weight_decay=1e-3, momentum=0.8)

train_step = make_train_step(model, loss_fnc, optimizer=OPTIMIZER)
validate = make_validate_fnc(model,loss_fnc)
losses=[]
val_losses = []

ValueError: The first argument to `Layer.call` must always be passed.

In [25]:
import wandb

In [26]:
from tensorflow.python.client import device_lib

print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 15489280208431014744
xla_global_id: -1
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 5748293632
locality {
  bus_id: 1
  links {
  }
}
incarnation: 4175917717449365301
physical_device_desc: "device: 0, name: NVIDIA GeForce RTX 3060 Ti, pci bus id: 0000:0b:00.0, compute capability: 8.6"
xla_global_id: 416903419
]


In [27]:

    for i in range(7):
        wandb.init(project="VGG_Training", entity='saransh17')
        learning_rate= 5e-5
        transfer_model.compile(loss="sparse_categorical_crossentropy", optimizer=keras.optimizers.Adam(lr=learning_rate), metrics=["accuracy"])
        history = transfer_model.fit(X_train, Y_train, batch_size = 1, epochs=50, validation_data=(X_test,Y_test))
        
        model.save(f'VGG_model_{i}.h5')
        
        loss, accuracy = transfer_model.evaluate(X_test, Y_test)
        print(f'Loss: {loss:.4f} - Accuracy: {accuracy:.4f}')
        wandb.log({"val_loss" : loss})

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: saransh17. Use `wandb login --relogin` to force relogin


c:\Users\Saransh\AppData\Local\Programs\Python\Python310\lib\site-packages\keras\optimizers\optimizer_v2\adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


InternalError: Failed copying input tensor from /job:localhost/replica:0/task:0/device:CPU:0 to /job:localhost/replica:0/task:0/device:GPU:0 in order to run _EagerConst: Dst tensor is not initialized.